In [1]:
# Run in terminal:
#pip install pypdf2
#pip install pycryptodome
%pip install pdfplumber
%pip install google-generativeai

Note: you may need to restart the kernel to use updated packages.
ERROR: Ignored the following versions that require a different python version: 0.1.0 Requires-Python >=3.9; 0.1.0rc1 Requires-Python >=3.8; 0.1.0rc2 Requires-Python >=3.8; 0.1.0rc3 Requires-Python >=3.9; 0.2.0 Requires-Python >=3.9; 0.2.1 Requires-Python >=3.9; 0.2.2 Requires-Python >=3.9; 0.3.0 Requires-Python >=3.9
ERROR: Could not find a version that satisfies the requirement google-generativeai (from versions: none)
ERROR: No matching distribution found for google-generativeai
Note: you may need to restart the kernel to use updated packages.


In [2]:

import google.generativeai as palm
import os

palm.configure(api_key=os.environ['API_KEY'])

ModuleNotFoundError: No module named 'google.generativeai'

## PDF to text
Extract PDF content to a string

In [2]:
import pdfplumber
import pandas as pd

def extract_text_from_pdf(pdf_path):
    with pdfplumber.open(pdf_path) as pdf:
        pdf_text=""
        for page in pdf.pages:
            pdf_text += page.extract_text()
    return pdf_text
        

In [6]:
text_pdf = extract_text_from_pdf("pdfs/bp-sustainability-report-2022.pdf")

['Reimagining energy',
 'for people and our planet',
 'bp sustainability report 2022Contents',
 'Sustainability at bp Getting to net zero 16 Engaging stakeholders 52 About our 2022 reporting',
 'Our sustainability frame 1 Our net zero ambition and aims 17 Engaging with our stakeholders 53',
 'Since we launched our sustainability frame we',
 'Our strategy and performance 2 Getting to net zero introduction 18 have worked to further embed sustainability',
 'Our reporting 56',
 'Letter from our chief executive officer 3 Net zero aims 1-5 update 19 across bp. We have also made progress',
 'Materiality 57 in a number of areas, which are covered in',
 'Letter from our EVP, strategy, Consistency of our ambition and',
 'About our reporting 58 this report.',
 'sustainability & ventures 4 aims with the Paris goals 20',
 '2022 at a glance 5 Five aims to get bp to net zero 21 Glossary 59 Our corporate reporting suite for 2022',
 'Assurance statement 61 comprises several elements, including this',
 

In [4]:
#split into sentences
def text_to_sentences(text):
    sentences = text.split('\n')
    return sentences

def create_sentence_chunks(sentences, chunk_size):
    sentence_chunks = [sentences[i:i+chunk_size] for i in range(0, len(sentences), chunk_size)]
    return sentence_chunks

def text_to_paragraph(text, chunk_size):
    return create_sentence_chunks(text_to_sentences(text), chunk_size)
    
chunk_size = 15
sentence_chunks = text_to_paragraph(text_pdf, chunk_size)
sentence_chunks

NameError: name 'text_pdf' is not defined

[['Reimagining energy',
  'for people and our planet',
  'bp sustainability report 2022Contents',
  'Sustainability at bp Getting to net zero 16 Engaging stakeholders 52 About our 2022 reporting',
  'Our sustainability frame 1 Our net zero ambition and aims 17 Engaging with our stakeholders 53',
  'Since we launched our sustainability frame we',
  'Our strategy and performance 2 Getting to net zero introduction 18 have worked to further embed sustainability',
  'Our reporting 56',
  'Letter from our chief executive officer 3 Net zero aims 1-5 update 19 across bp. We have also made progress',
  'Materiality 57 in a number of areas, which are covered in'],
 ['Letter from our EVP, strategy, Consistency of our ambition and',
  'About our reporting 58 this report.',
  'sustainability & ventures 4 aims with the Paris goals 20',
  '2022 at a glance 5 Five aims to get bp to net zero 21 Glossary 59 Our corporate reporting suite for 2022',
  'Assurance statement 61 comprises several elements, in

In [10]:
data = []

# Iterate through sentence chunks
for idx, chunk in enumerate(sentence_chunks, start=1):
    
    # Merge sentences within the chunk into one string
    merged_text = ''.join(chunk)
    
    # Append data to the list
    data.append({
        'paragraph_number':idx,
        'text':merged_text
    })

# DataFrame with different paragraphs
df =pd.DataFrame(data)

df

paragraph_number                                               text
0                   1  Reimagining energyfor people and our planetbp ...
1                   2  Letter from our EVP, strategy, Consistency of ...
2                   3  bp.com/quickreadAim 3: Net zero sales 25‘Who w...
3                   4  Policies and practices 12 bp Annual Report 202...
4                   5  Aim 12: Just transition 39Aim 13: Sustainable ...
..                ...                                                ...
300               301  forecasts, projections and forward-looking sol...
301               302  ‘anticipates’, ‘plans’, ‘we see’ or similar ex...
302               303  for customers; plans and expectations regardin...
303               304  over time; plans and expectations regarding ex...
304               305  facebook.com/bplinkedin.com/company/bpinstagra...

[305 rows x 2 columns]

## Embeddings

In [98]:
from vertexai.preview.language_models import TextEmbeddingModel

# model = TextEmbeddingModel.from_pretrained("textembedding-gecko@001")
model = TextEmbeddingModel.from_pretrained("textembedding-gecko@002")

In [99]:
import json
import time

import numpy as np
import pandas as pd

In [100]:
def get_embedding(text):
    get_embedding.counter += 1
    try:
        if get_embedding.counter % 100 == 0:
            time.sleep(3)
        return model.get_embeddings([text])[0].values #Send request to embedding model
    except:
        print('waiting for 60 secs')
        time.sleep(60)
        return model.get_embeddings([text])[0].values #Send request to embedding model


get_embedding.counter = 0

# This may take several minutes to complete.
df["embedding"] = df["text"].apply(lambda x: get_embedding(x))

# Convert the embeddings into a Python list 
embeddings_list = df['embedding'].values.tolist()

waiting for 60 secs
waiting for 60 secs


In [101]:
embeddings_list

[[-0.027620328590273857,
  -0.017222948372364044,
  -0.018571704626083374,
  0.0034746332094073296,
  0.012131390161812305,
  -0.004055713769048452,
  0.003249815432354808,
  0.0022142184898257256,
  -0.0173239354044199,
  0.0017461283132433891,
  0.018082819879055023,
  0.017343241721391678,
  0.04053612798452377,
  -0.008937151171267033,
  -0.05578802153468132,
  -0.007336893584579229,
  -0.00295836478471756,
  0.0048019071109592915,
  0.00697451364248991,
  -0.0030020629055798054,
  -0.0783863365650177,
  -0.006598502863198519,
  -0.0006694989278912544,
  0.005605613812804222,
  -0.0008469006279483438,
  -0.09024020284414291,
  -0.007911710999906063,
  0.021836107596755028,
  -0.0328805074095726,
  0.023755326867103577,
  -0.015426132827997208,
  0.015854744240641594,
  -0.04039888083934784,
  -0.026136113330721855,
  -0.019495896995067596,
  -0.009745292365550995,
  0.016180021688342094,
  0.012391038239002228,
  -0.010908988304436207,
  0.0034107519313693047,
  0.01293807011097669

## Generate Embedding File

In [15]:
import json

#Specify the desired path and filename
json_path = 'data/vector_search_dataset.json'

# Create empty dictionary to be saved as JSON file
empty_data = []

# Write the empty dictionary to a JSON file
with open(json_path, "w") as json_file:
    json.dump(empty_data, json_file)
    
print(f"Empty JOSN file created at: {json_path}")

Empty JOSN file created at: data/vector_search_dataset.json


In [102]:
with open("data/vector_search_dataset.json", "w", encoding='UTF-8') as f:
    for i in range(len(embeddings_list)):
        json_object = json.dumps({
            'id': str(i),
            'embedding': embeddings_list[i]
        })
        f.write(json_object)
        f.write('\n')

## Copy Dataset to Storage Bucket

In [103]:
PROJECT_ID = !gcloud config get project
PROJECT_ID = PROJECT_ID.n
LOCATION = "europe-west2"
LOCATION_DEPLOY = "europe-west2" #Location to deploy GCP resources

import vertexai
from google.cloud import aiplatform

vertexai.init(project=PROJECT_ID, location=LOCATION)

In [104]:
!mkdir -p data
!gsutil copy data/vector_search_dataset.json gs://gen-ai-{PROJECT_ID}-bucket/embeddings/vs_root/vector_search_dataset.json

Copying file://data/vector_search_dataset.json [Content-Type=application/json]...
/ [1 files][  5.0 MiB/  5.0 MiB]                                                
Operation completed over 1 objects/5.0 MiB.                                      


## Create indexes and index endpoints to apply ANN

In [105]:
DIMENSIONS = 768
GS_URI = "gs://gen-ai-%s-bucket/embeddings/vs_root/" % PROJECT_ID

# Create indexes (for each embeddings?)
gen_ai_index = aiplatform.MatchingEngineIndex.create_tree_ah_index(
    display_name="Gen AI Index",
    contents_delta_uri=GS_URI,
    dimensions=DIMENSIONS,
    approximate_neighbors_count=5,
    distance_measure_type="DOT_PRODUCT_DISTANCE",
    leaf_node_embedding_count=10,
    leaf_nodes_to_search_percent=80,
    description="Example Index for Gen AI Playpen",
    location=LOCATION_DEPLOY
)

Creating MatchingEngineIndex
Create MatchingEngineIndex backing LRO: projects/774552106847/locations/europe-west2/indexes/7796434642420105216/operations/66127927829331968
MatchingEngineIndex created. Resource name: projects/774552106847/locations/europe-west2/indexes/7796434642420105216
To use this MatchingEngineIndex in another session:
index = aiplatform.MatchingEngineIndex('projects/774552106847/locations/europe-west2/indexes/7796434642420105216')


In [106]:
# Create index endpoints so the indexes can receive queries
gen_ai_index_endpoint = aiplatform.MatchingEngineIndexEndpoint.create(
    display_name="Gen AI Index Endpoint",
    description="Example Index for Gen AI Playpen",
    public_endpoint_enabled=True,
    location=LOCATION_DEPLOY
)

Creating MatchingEngineIndexEndpoint
Create MatchingEngineIndexEndpoint backing LRO: projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248/operations/2798687001736380416
MatchingEngineIndexEndpoint created. Resource name: projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248
To use this MatchingEngineIndexEndpoint in another session:
index_endpoint = aiplatform.MatchingEngineIndexEndpoint('projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248')


In [109]:
# Deploy the index endpoints
gen_ai_index_endpoint = gen_ai_index_endpoint.deploy_index(
    index=gen_ai_index, deployed_index_id= "gen_ai_deployed_index2", #"gen_ai_deployed_index1",
    machine_type="e2-standard-16",
    min_replica_count=1,
    max_replica_count=1
)

gen_ai_index_endpoint.deployed_indexes


Deploying index MatchingEngineIndexEndpoint index_endpoint: projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248
Deploy index MatchingEngineIndexEndpoint index_endpoint backing LRO: projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248/operations/5613436768842940416
MatchingEngineIndexEndpoint index_endpoint Deployed index. Resource name: projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248


[id: "gen_ai_deployed_index2"
index: "projects/774552106847/locations/europe-west2/indexes/7796434642420105216"
create_time {
  seconds: 1702398825
  nanos: 824317000
}
index_sync_time {
  seconds: 1702399733
  nanos: 884340000
}
deployment_group: "default"
dedicated_resources {
  machine_spec {
    machine_type: "e2-standard-16"
  }
  min_replica_count: 1
  max_replica_count: 1
}
]

In [113]:
# functions to retrieve indexes and index endpoints as python objects

INDEX_ENDPOINT_name = "projects/774552106847/locations/europe-west2/indexEndpoints/4804918589939253248"
INDEX_name = "projects/774552106847/locations/europe-west2/indexes/7796434642420105216"



gen_ai_index_endpoint = aiplatform.MatchingEngineIndexEndpoint(
    index_endpoint_name=INDEX_ENDPOINT_name
)

gen_ai_index = aiplatform.MatchingEngineIndex(
    index_name=INDEX_name
)

## Create Online Queries

Pre-define function that generates an embedding for an input prompt using the embeddings-gecko model and performs a search.

In [114]:
NUM_NEIGHBOURS = 3 #Number of neighbours from query

def search(input):
    embedding_vec =  model.get_embeddings([input])[0].values #Send request to embedding model to generate the embedding vector
    
    #find neighbours using vector search
    neighbours = gen_ai_index_endpoint.find_neighbors(
        deployed_index_id="gen_ai_deployed_index2",
        queries=[embedding_vec],
        num_neighbors=NUM_NEIGHBOURS,
    )[0]
    
    for nb in neighbours:
        print("id: " + nb.id + " | text: " + df.iloc[int(nb.id)]["text"] + " | dist: " + str(nb.distance)) 

In [116]:
search("how much emissions for scope 1 2 and 3 in 2020?")

id: 102 | text: Progress and targets45.5Reduction in emissions against the 2019 baseline Scope 1 (direct) and Scope 2 (indirect) GHG(absolute basis). emissions (operational control boundary)b35.6 (MtCOe)16% 2020 performance 231.9 60 5.235% 2021 performance3.841% 2022 performance 49.2 | dist: 0.9111103415489197
id: 103 | text: 40 2.441.7 1.520% 2025 target33.230.450% 2030 aim 20Net zero 2050 or sooner02019 2020 2021 2022Scope 1 | dist: 0.8981072902679443
id: 87 | text: Aims Measure/coverage 2019 2020 update 2021 performance 2022 performance 2025 targets 2030 aims Aims for 2050or soonerBaselineAim 1 Scope 50%a54.4 16%a 35%a 41%a 20%a Net zeroNet zero operations 1+230-35%bMtCOe2 | dist: 0.889756441116333


## Final Model

In [117]:
from vertexai.preview.language_models import ChatModel

""" 
between using the most stable model in the last 6 month: chat-bison@001 
and the latest, most capable model, there is a massive difference in 
terms of context awareness, length of answer, ability to follow instructions,
etc. How do we measure these using metrics? I'm working on it.

I lied, the latest model, whilst sometimes its answers can be amazing,
definitely not as good when using RAG, it ignores context too often,
until I fix that, we'll work with the stable version.

"""
class PaLMWrapper:
    def __init__(self):
        self.chat_model = ChatModel.from_pretrained("chat-bison@002")
        self.parameters = {
            "temperature": 0,
            "max_output_tokens": 256,
            "top_p": 0.95,
        }
    
    def generate_response(self, context, message):
        chat = self.chat_model.start_chat(context=context)
        response = chat.send_message(message, **self.parameters)
        return response.text

In [118]:
pw = PaLMWrapper()

In [123]:
class VertexAIVectorStore:
    def __init__(self):
        
        # god awful way of doing it, should be a config and passed through but oh well hacky hack
        self.gen_ai_index_endpoint = aiplatform.MatchingEngineIndexEndpoint(
            index_endpoint_name=INDEX_ENDPOINT_name
        )

        self.gen_ai_index = aiplatform.MatchingEngineIndex(
            index_name=INDEX_name
        )
        
        self.model = TextEmbeddingModel.from_pretrained("textembedding-gecko@001")
        self.df = df
        
    def search(self, input, k=3):
        embedding_vec =  self.model.get_embeddings([input])[0].values #Send request to embedding model to generate the embedding vector

        #find neighbours using vector search
        neighbours = self.gen_ai_index_endpoint.find_neighbors(
            deployed_index_id="gen_ai_deployed_index2",
            queries=[embedding_vec],
            num_neighbors=k,
        )[0]
        
        results = []
        for nb in neighbours:
            nb_id = int(nb.id)
            if nb_id < len(self.df):
                paragraph_num = self.df.iloc[int(nb.id)]['paragraph_number']
                text = self.df.iloc[int(nb.id)]['text']
                score = nb.distance
                results.append((paragraph_num, text, score))
            else:
                results=[('', '', 0)]
        
        return results

In [124]:
vai = VertexAIVectorStore()

In [125]:
# couldnt get langchain to work so custom RAG anyone?
import time

class RAG:
    def __init__(self, vector_store, palm_wrapper, initial_system_prompt=True):
        self.vector_store = vector_store
        self.palm_wrapper = palm_wrapper
        # the comment from mathew regarding memory
        self.conversation_history = []
        
        if initial_system_prompt:            
            system_prompt = r"You are a professional assistant with extensive experience helping numerous small and medium businesses. You work for a large retail bank called Lloyds. Please assist the user answering questions with detailed responses, providing reasoning whenever prescriptive advice is given. Ensure your answers are elaborate and helpful."
            self.conversation_history.append((system_prompt, ""))
        
    
    def generate(self, query, is_user_query=True, k=3):
        vector_start_time = time.time()
        
        contexts=[]
        sources=[]
        scores=[]
        
        if is_user_query:
            # if user query, perform vector db search
            # retrieve contexts based on the query
            search_results = self.vector_store.search(query, k)
            contexts = [str(result[1]) for result in search_results]
            sources = [result[0] for result in search_results]
            scores = [result[2] for result in search_results]
            
            if scores[0] < 0.66:
                for i in range(len(contexts)):
                    
                    contexts[i]='You are a professional assistant with extensive experience helping numerous small and medium businesses. You work for a large retail bank called Lloyds. Please assist the user answering questions with detailed responses, providing reasoning whenever prescriptive advice is given. Ensure your answers are elaborate and helpful. In your search you could not find relevant context within the dataset. Therefore, you are uncertain about your response. IMPORTANT: Remind the customer that you are built to answer Lloyds banking related questions only.'
                    sources[i]='Could not find relevant sources'
            
              
        vector_end_time = time.time()
        # combine both query and response from conversation history
        history_context = '\n'.join(['Q: ' + query + '\nA: ' + response for query, response in self.conversation_history[-k:]])
        
        # combine history context and current contexts
        combined_context = '\n'.join(contexts + [history_context][-7500:])
        combined_context = combined_context[-30000:]
        
        lm_start_time = time.time()
        response = self.palm_wrapper.generate_response(combined_context, query)
        lm_end_time = time.time()
        # update conversation history with current interaction
        self.conversation_history.append((query, response))
        
        vector_search_time = vector_end_time - vector_start_time
        lm_inference_time = lm_end_time - lm_start_time
        # removed , vector_search_time, lm_inference_time from return
        return response, sources, scores

In [126]:
rag = RAG(vai, pw)
query = "What are the main actions taken for sustainability?"
response, sources, scores = rag.generate(query)
print(query)
print(response)
print('sources used:', sources)
print('scores:', scores)
print("\n")


query = " scope 3 emissions in Mt Co2?"
print(query)
response, sources, scores = rag.generate(query)
print(response)
print('sources used:', sources)
print('scores:', scores)
print("\n")

query = "scope 1 and 2 emissions in Mt CO2?"
print(query)
response, sources, scores = rag.generate(query)
print(response)
print('sources used:', sources)
print('scores:', scores)
print("\n")

query = "scope 1 and 2 absolute emissions?"
print(query)
response, sources, scores = rag.generate(query)
print(response)
print('sources used:', sources)
print('scores:', scores)
print("\n")

query = "target reduction in scope 1 and 2?"
print(query)
response, sources, scores = rag.generate(query)
print(response)
print('sources used:', sources)
print('scores:', scores)


What are the main actions taken for sustainability?
 Our approach to sustainability encompasses various actions to drive positive change across our operations and value chain. Here are the main actions we take:

1. **Reducing Greenhouse Gas Emissions:** We aim to reduce our operational emissions by 35-40% by 2030 and achieve net zero by 2050. This involves transitioning to renewable energy sources, improving energy efficiency, and investing in low-carbon technologies.

2. **Promoting Circularity:** We are committed to reducing waste and promoting a circular economy. This includes designing products for recyclability, increasing the use of recycled materials, and exploring innovative waste management solutions.

3. **Enhancing Biodiversity:** We recognize the importance of biodiversity for the health of our planet and communities. We work to minimize our impact on ecosystems, protect and restore habitats, and support conservation initiatives.

4. **Respecting Human Rights:** We uphold t

In [129]:
query = "Give me the scope emissions in MtCO2e per year per scope 1 to 3"
print(query)
response, sources, scores = rag.generate(query)
print(response)
print('sources used:', sources)
print('scores:', scores)

Give me the scope emissions in MtCO2e per year per scope 1 to 3
 **Scope 1 emissions (MtCO2e)**
- 2019: 638
- 2020: 573
- 2021: 553
- 2022: 538

**Scope 2 emissions (MtCO2e)**
- 2019: 355
- 2020: 340
- 2021: 330
- 2022: 325

**Scope 3 emissions (MtCO2e)**
- 2019: 1,638
- 2020: 1,565
- 2021: 1,523
- 2022: 1,475
sources used: [127, 128, 294]
scores: [0.7803692817687988, 0.7660687565803528, 0.7549788951873779]


In [130]:
df.iloc[126]['text'] + df.iloc[127]['text'] + df.iloc[293]['text']

'2019 2020 2021 2022 zero production).993MtCO 2e to 1,638MtCO 2e. Overall, the 2019 Each of these activities may have beencarbon intensity remained at 79gCO 2e/MJ. Average emissions intensity At a high level, it is straightforwarde – because, completed by bp or other companies, so theof energy products 79 77 78 77 by covering the full ‘lifecycle’ emissionsemissions from those activities could be Scope 1,All figures, up to and including our baselineRefined energy products 95 92 92 92 associated with the energy products we sell Scope 2 or Scope 3 emissions for bp. Either way,year of 2019, have been recalculated on this(see the graphic above), aim 3 covers many ofrevised basis. Gas products 68 67 67 67 aim 3 covers those emissions (‘Production’,the emissions that people might think of as bp’s‘Processing’, ‘Transportation’ or DistributionBioproducts 47 44 43 43 Scope 1, 2 or 3 emissions:emissions in the graphic above).Power productsc 57 59 56 52 y Such as when someone drives a vehicleOur p

In [97]:

query = "scope 1+2 absolute emissions for different years?"
response, sources, scores = rag.generate(query)
print(query)
print(response)
print('sources used:', sources)
print('scores:', scores)
print("\n")

# query = "scope 3 asbolute emission in 2019 baseline?"
# response, sources, scores = rag.generate(query)
# print(query)
# print(response)
# print('sources used:', sources)
# print('scores:', scores)
# print("\n")


# query = "scope 1 and 2 reudction percentage in 2020?"
# response, sources, scores = rag.generate(query)
# print(query)
# print(response)
# print('sources used:', sources)
# print('scores:', scores)
# print("\n")

scope 1+2 absolute emissions for different years?
 Our Scope 1 and 2 absolute emissions for different years are as follows:

- 2019: 359.6 MtCO2e
- 2020: 231.9 MtCO2e
- 2021: 202.7 MtCO2e
- 2022: 172.5 MtCO2e

We have made significant progress in reducing our Scope 1 and 2 emissions over the past few years, and we are committed to continuing this trend in the future. We believe that reducing our emissions is essential to mitigating climate change and protecting the environment for future generations.
sources used: [103, 127, 294]
scores: [0.7637061476707458, 0.7615953087806702, 0.7554951310157776]




In [86]:
#Check chunks used for ans 1: "Scope 3 emissions in 2019 were 1,638 MtCO2."
#index chunks wiht source_number - 1
df.iloc[102]['text'] + df.iloc[126]['text'] + df.iloc[126]['text']

'Progress and targets45.5Reduction in emissions against the 2019 baseline Scope 1 (direct) and Scope 2 (indirect) GHG(absolute basis). emissions (operational control boundary)b35.6 (MtCOe)16% 2020 performance 231.9 60 5.235% 2021 performance3.841% 2022 performance 49.22019 2020 2021 2022 zero production).993MtCO 2e to 1,638MtCO 2e. Overall, the 2019 Each of these activities may have beencarbon intensity remained at 79gCO 2e/MJ. Average emissions intensity At a high level, it is straightforwarde – because, completed by bp or other companies, so theof energy products 79 77 78 77 by covering the full ‘lifecycle’ emissionsemissions from those activities could be Scope 1,All figures, up to and including our baselineRefined energy products 95 92 92 92 associated with the energy products we sell Scope 2 or Scope 3 emissions for bp. Either way,year of 2019, have been recalculated on this(see the graphic above), aim 3 covers many ofrevised basis. Gas products 68 67 67 67 aim 3 covers those emis

In [95]:
#Check chunks used for ans 1: " Our Scope 1 and 2 absolute emissions in 2019 were 359.6 MtCO2e."
#index chunks wiht source_number - 1
df.iloc[102]['text'] + df.iloc[126]['text'] + df.iloc[293]['text']

# Text used:
#'Progress and targets45.5Reduction in emissions against the 2019 baseline Scope 1 (direct) and Scope 2 (indirect) GHG(absolute basis).emissions (operational control boundary)b35.6 (MtCOe)16% 2020 performance 231.9 60 5.235% 2021 performance3.841% 2022 performance 49.22019 2020 2021 2022 zero production).993MtCO 2e to 1,638MtCO 2e. Overall, the 2019 Each of these activities may have beencarbon intensity remained at 79gCO 2e/MJ. Average emissions intensity At a high level, it is straightforwarde – because, completed by bp or other companies, so theof energy products 79 77 78 77 by covering the full ‘lifecycle’ emissionsemissions from those activities could be Scope 1,All figures, up to and including our baselineRefined energy products 95 92 92 92 associated with the energy products we sell Scope 2 or Scope 3 emissions for bp. Either way,year of 2019, have been recalculated on this(see the graphic above), aim 3 covers many ofrevised basis. Gas products 68 67 67 67 aim 3 covers those emissions (‘Production’,production and assuming that all produced volumes and the reduction is expected to be ongoing.undergo full stoichiometric combustion to CO 2). Reductions are reportable for a 12-month periodAim 2 is bp’s Scope 3 aim and relates to Scope 3 from the start of the intervention/action.category 11 emissions. Any interim target or aim inrespect of bp’s aim 2 is defined in terms of absolutereductions relative to the baseline year of 2019.For terms with refer to the glossary on pages 59-60.60 bp sustainability report 2022Our reportingAssurance statementIndependent assurance statement by Deloitte LLP to bp on selected sustainability information'
# making up numbers

'Progress and targets45.5Reduction in emissions against the 2019 baseline Scope 1 (direct) and Scope 2 (indirect) GHG(absolute basis). emissions (operational control boundary)b35.6 (MtCOe)16% 2020 performance 231.9 60 5.235% 2021 performance3.841% 2022 performance 49.22019 2020 2021 2022 zero production).993MtCO 2e to 1,638MtCO 2e. Overall, the 2019 Each of these activities may have beencarbon intensity remained at 79gCO 2e/MJ. Average emissions intensity At a high level, it is straightforwarde – because, completed by bp or other companies, so theof energy products 79 77 78 77 by covering the full ‘lifecycle’ emissionsemissions from those activities could be Scope 1,All figures, up to and including our baselineRefined energy products 95 92 92 92 associated with the energy products we sell Scope 2 or Scope 3 emissions for bp. Either way,year of 2019, have been recalculated on this(see the graphic above), aim 3 covers many ofrevised basis. Gas products 68 67 67 67 aim 3 covers those emis

In [ ]:
#Check chunks used for ans 1: "Scope 3 emissions in 2019 were 1,638 MtCO2."
#index chunks wiht source_number - 1
df.iloc[102]['text'] + df.iloc[126]['text'] + df.iloc[127]['text']

In [ ]:
folder_path = 'output'
data = {'file_name' : [], 'text': [], 'url': []}

for filename in os.listdir(folder_path):
    if filename.endswith('.txt'):
        file_path = os.path.join(folder_path, filename)
        with open(file_path, 'r', encoding='utf-8') as file:
            lines = file.readlines()
        
        if lines:
            url = lines[-1].strip()
            text_data = ''.join(lines[:-1]).replace('\n', '')
        
            data['file_name'].append(filename)
            data['url'].append(url)
            data['text'].append(text_data)

text_data_df = pd.DataFrame(data)
text_data_df.to_csv('text_data.csv', index=False)

print(text_data_df.head(2))

In [24]:
from transformers import pipeline

2023-12-11 11:42:12.784971: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-12-11 11:42:14.263712: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda/lib64:/usr/local/nccl2/lib:/usr/local/cuda/extras/CUPTI/lib64
2023-12-11 11:42:14.263871: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /usr/local/cuda/lib64:/usr/local/nccl2/lib:/usr/loca

In [ ]:
model = 
tokenizer = 